# Instalación del paquete
En el caso de ejecutar este Notebook en un entorno Cloud como Google Colab o Kaggle, debes descomentar el siguiente comando para permitir la instalación del paquete de Python `blackops` desarrollado para este curso.

In [1]:
# !pip install git+https://github.com/donielix/esic-bigdata-iv-blackops.git > /dev/null

# Importación de módulos necesarios
Para leer los datos se necesita disponer de un fichero denominado `config.share`, puesto que es la llave de acceso al almacenamiento Cloud en donde residen físicamente las tablas. Lo más cómodo es situar dicho archivo en la misma ruta en que se ubica este Notebook, pero también puede localizarse en otra ruta y hacer referencia a la misma dentro de la función `read_table`, que acepta un argumento denominado `config_share_path`.

In [2]:
from blackops.utils.catalog import read_table
import pyspark.sql.functions as f
import pyspark.sql.types as t
import plotly.express as px
import pandas as pd

Ahora realizaremos la lectura de una tabla llamada `cybersecurity_attacks`, a través de la función `read_table`. En este caso, asumiremos que el fichero `config.share` se encuentra ubicado exactamente en la misma ruta en la que se encuentra este notebook, y por tanto no es necesario incluir el argumento `config_share_path`. Para más información, recuerda la utilidad de consultar la documentación de cada función que se vaya a utilizar, utilizando el símbolo de interrogación (`read_table?`).

In [3]:
df = read_table(table_name="cybersecurity_attacks")

24/10/20 20:45:56 WARN Utils: Your hostname, pop-os resolves to a loopback address: 127.0.1.1; using 192.168.1.35 instead (on interface enp3s0)
24/10/20 20:45:56 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Ivy Default Cache set to: /home/dadiego/.ivy2/cache
The jars for the packages stored in: /home/dadiego/.ivy2/jars
io.delta#delta-spark_2.12 added as a dependency
io.delta#delta-sharing-spark_2.12 added as a dependency
:: resolving dependencies :: org.apache.spark#spark-submit-parent-2231a956-abc3-4ed9-8918-c90feeb476a3;1.0
	confs: [default]


:: loading settings :: url = jar:file:/home/dadiego/projects/ESIC/esic-bigdata-iv-blackops/.venv/lib/python3.10/site-packages/pyspark/jars/ivy-2.5.1.jar!/org/apache/ivy/core/settings/ivysettings.xml


	found io.delta#delta-spark_2.12;3.2.0 in central
	found io.delta#delta-storage;3.2.0 in central
	found org.antlr#antlr4-runtime;4.9.3 in central
	found io.delta#delta-sharing-spark_2.12;3.2.0 in central
	found io.delta#delta-sharing-client_2.12;1.0.5 in central
	found org.apache.httpcomponents#httpclient;4.5.13 in central
	found org.apache.httpcomponents#httpcore;4.4.13 in central
	found commons-logging#commons-logging;1.2 in central
	found commons-codec#commons-codec;1.11 in central
:: resolution report :: resolve 222ms :: artifacts dl 7ms
	:: modules in use:
	commons-codec#commons-codec;1.11 from central in [default]
	commons-logging#commons-logging;1.2 from central in [default]
	io.delta#delta-sharing-client_2.12;1.0.5 from central in [default]
	io.delta#delta-sharing-spark_2.12;3.2.0 from central in [default]
	io.delta#delta-spark_2.12;3.2.0 from central in [default]
	io.delta#delta-storage;3.2.0 from central in [default]
	org.antlr#antlr4-runtime;4.9.3 from central in [default]
	

Veamos la descripción de las columnas del dataset, con explicaciones detalladas para facilitar la comprensión de cada campo:

- **Timestamp**: El momento exacto en el que ocurrió la actividad de red.
  - **Explicación**: Indica la fecha y la hora en la que sucedió el tráfico en la red. Es útil para identificar cuándo ocurrieron los eventos y en qué orden.  
  - **Ejemplo**: "2023-05-30 08:33:58" significa que el evento ocurrió el 30 de mayo de 2023 a las 8:33:58 a.m.

- **Source IP Address**: La dirección IP del emisor o iniciador del tráfico de red.
  - **Explicación**: Es la dirección desde donde se origina la comunicación o ataque. Permite rastrear al dispositivo que inició la conexión o el ataque.
  - **Ejemplo**: "103.216.15.12" es la dirección IP desde la que se envió el paquete.

- **Destination IP Address**: La dirección IP del receptor o destino del tráfico de red.
  - **Explicación**: Es la dirección IP del dispositivo que recibe el tráfico o es el objetivo del ataque.
  - **Ejemplo**: "84.9.164.252" es la dirección IP del dispositivo que recibió el paquete.

- **Source Port**: El número de puerto utilizado por la dirección IP de origen.
  - **Explicación**: Los puertos son puntos de acceso virtuales que las computadoras utilizan para diferenciar tipos de tráfico. Este campo identifica el puerto del emisor.
  - **Ejemplo**: "31225" es el número de puerto desde el cual se envió el tráfico.

- **Destination Port**: El número de puerto utilizado por la dirección IP de destino.
  - **Explicación**: Similar al puerto de origen, pero se refiere al puerto del receptor. Determina qué aplicación está esperando el tráfico.
  - **Ejemplo**: "17616" es el número de puerto donde el receptor esperaba recibir la comunicación.

- **Protocol**: El protocolo de comunicación utilizado (e.g., TCP, UDP, ICMP).
  - **Explicación**: Los protocolos definen cómo se debe enviar y recibir la información. Los más comunes son TCP, UDP e ICMP.
  - **Ejemplo**: "ICMP" es un protocolo utilizado, por ejemplo, para comprobar la disponibilidad de un dispositivo (como con el comando "ping").

- **Packet Length**: El tamaño del paquete en bytes.
  - **Explicación**: El tamaño total del paquete de datos transmitido por la red, medido en bytes.
  - **Ejemplo**: "503" significa que el paquete contiene 503 bytes de información.

- **Packet Type**: Tipo de paquete (e.g., paquete de datos, paquete de control).
  - **Explicación**: Indica si el paquete contiene datos útiles para la comunicación (paquete de datos) o está destinado a controlar la comunicación (paquete de control).
  - **Ejemplo**: "Data" significa que el paquete contiene datos transmitidos, mientras que "Control" implica que es un paquete de gestión.

- **Traffic Type**: El tipo de tráfico (e.g., tráfico web, tráfico de correo electrónico).
  - **Explicación**: Clasifica el tipo de datos que se están enviando por la red. Ayuda a entender el contexto del tráfico, como si es navegación web, correo electrónico, etc.
  - **Ejemplo**: "HTTP" indica que es tráfico web.

- **Payload Data**: Los datos reales transmitidos en el paquete.
  - **Explicación**: El contenido o la carga útil del paquete, que puede ser cualquier tipo de información, como texto, imágenes, o archivos.
  - **Ejemplo**: "Qui natus odio asperiores nam..." es un extracto de los datos enviados en este paquete.

- **Malware Indicators**: Indicadores de actividad potencialmente maliciosa o presencia de malware.
  - **Explicación**: Señales que indican que el paquete puede estar asociado con un ataque o contener malware, como patrones reconocidos de actividad maliciosa.
  - **Ejemplo**: "IoC Detected" significa que se detectaron Indicadores de Compromiso (IoC), que son señales de posibles amenazas.

- **Anomaly Scores**: Puntuaciones que indican desviaciones del comportamiento esperado, utilizadas para la detección de anomalías.
  - **Explicación**: Un puntaje que cuantifica lo inusual que es el comportamiento del tráfico, siendo útil para la detección automática de amenazas.
  - **Ejemplo**: "28.67" es un valor que indica la gravedad de la anomalía detectada.

- **Alerts/Warnings**: Notificaciones o advertencias generadas por sistemas de seguridad o herramientas de monitoreo.
  - **Explicación**: Avisos automáticos generados por sistemas de defensa cuando se detecta tráfico sospechoso.
  - **Ejemplo**: "Alert Triggered" indica que un sistema ha generado una alerta por actividad sospechosa.

- **Attack Type**: Tipo de ataque detectado o sospechado (e.g., DDoS, SQL injection).
  - **Explicación**: Clasifica el tipo de ataque, lo que puede ayudar a identificar qué tipo de amenaza está ocurriendo.
  - **Ejemplo**: "Malware" o "DDoS" son tipos de ataques comunes.

- **Attack Signature**: Patrones o firmas específicos asociados con ataques conocidos.
  - **Explicación**: Identificadores que coinciden con ataques previamente observados o conocidos, utilizados para identificar amenazas de manera automática.
  - **Ejemplo**: "Known Pattern B" se refiere a un patrón conocido de ataque de malware.

- **Action Taken**: Acciones realizadas en respuesta a las amenazas o anomalías detectadas.
  - **Explicación**: Muestra las contramedidas o respuestas que se tomaron al detectar un ataque, como bloquear el tráfico o solo registrarlo.
  - **Ejemplo**: "Blocked" significa que el tráfico fue bloqueado, mientras que "Logged" indica que solo se registró.

- **Severity Level**: El nivel de severidad asociado con una alerta o evento (e.g., bajo, medio, alto).
  - **Explicación**: Mide la gravedad del incidente detectado, lo que puede guiar la prioridad de las acciones.
  - **Ejemplo**: "Low" indica que el evento tiene una baja severidad.

- **User Information**: Información sobre el usuario involucrado en la actividad de red.
  - **Explicación**: Identifica al usuario que estaba asociado con la actividad de red, ya sea el dueño del dispositivo o una cuenta de usuario.
  - **Ejemplo**: "Reyansh Dugal" es el nombre del usuario asociado al tráfico.

- **Device Information**: Información sobre el dispositivo involucrado en la actividad de red (e.g., tipo de dispositivo, sistema operativo).
  - **Explicación**: Detalles sobre el equipo o dispositivo desde el cual se originó o recibió el tráfico, como el sistema operativo o tipo de navegador.
  - **Ejemplo**: "Mozilla/5.0 (compatible; MSIE 8.0; Windows NT 6.2; Trident/5.0)" es una cadena de identificación del navegador.

- **Network Segment**: El segmento o subred de la red donde ocurrió la actividad.
  - **Explicación**: La parte de la red donde se detectó el tráfico, útil para identificar áreas afectadas.
  - **Ejemplo**: "Segment A" identifica una parte específica de la red.

- **Geo-location Data**: Información de localización geográfica asociada con las direcciones IP.
  - **Explicación**: Proporciona la ubicación física aproximada del dispositivo según su IP, lo que puede ser útil para detectar tráfico fuera de lo común.
  - **Ejemplo**: "Jamshedpur, Sikkim" indica la ciudad y el estado donde está registrada la dirección IP.

- **Proxy Information**: Información sobre servidores proxy involucrados en la comunicación de red.
  - **Explicación**: Si la comunicación pasa por un servidor proxy, este campo indica los detalles del proxy, lo que puede ayudar a identificar intermediarios en la conexión.
  - **Ejemplo**: "150.9.97.135" es una dirección IP asociada con un servidor proxy.

- **Firewall Logs**: Registros generados por dispositivos de firewall que indican tráfico permitido o bloqueado.
  - **Explicación**: Registra las acciones realizadas por el firewall, como si bloqueó o permitió el tráfico.
  - **Ejemplo**: "Log Data" indica que el tráfico fue registrado por el firewall.

- **IDS/IPS Alerts**: Alertas generadas por Sistemas de Detección de Intrusos (IDS) o Sistemas de Prevención de Intrusos (IPS) que indican actividad sospechosa o maliciosa.
  - **Explicación**: Avisos generados cuando un sistema IDS o IPS detecta tráfico malicioso o inusual.
  - **Ejemplo**: "Alert Data" indica que una alerta fue generada.

- **Log Source**: El origen o fuente de la entrada de registro (e.g., nombre del sistema o dispositivo que genera el log).
  - **Explicación**: El sistema que generó los datos de registro.
  - **Ejemplo**: "Server" o "Firewall" son ejemplos de posibles fuentes de registros.

# Vista general del DataFrame
Lo primero de todo es comprobar cuál es el esquema del DataFrame (las columnas y sus tipos) y obtener una vista general de sus primeros datos

In [4]:
df.printSchema()

root
 |-- Timestamp: timestamp (nullable = true)
 |-- Source IP Address: string (nullable = true)
 |-- Destination IP Address: string (nullable = true)
 |-- Source Port: long (nullable = true)
 |-- Destination Port: long (nullable = true)
 |-- Protocol: string (nullable = true)
 |-- Packet Length: long (nullable = true)
 |-- Packet Type: string (nullable = true)
 |-- Traffic Type: string (nullable = true)
 |-- Payload Data: string (nullable = true)
 |-- Malware Indicators: string (nullable = true)
 |-- Anomaly Scores: double (nullable = true)
 |-- Alerts/Warnings: string (nullable = true)
 |-- Attack Type: string (nullable = true)
 |-- Attack Signature: string (nullable = true)
 |-- Action Taken: string (nullable = true)
 |-- Severity Level: string (nullable = true)
 |-- User Information: string (nullable = true)
 |-- Device Information: string (nullable = true)
 |-- Network Segment: string (nullable = true)
 |-- Geo-location Data: string (nullable = true)
 |-- Proxy Information: strin

Con el método `limit` podemos restringir el número de registros que mostrar

In [5]:
df.limit(5)

24/10/20 20:46:04 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+-------------------+-----------------+----------------------+-----------+----------------+--------+-------------+-----------+------------+------------------------------------------------------------------------------------------------------------------------------------------------------+------------------+--------------+---------------+-----------+----------------+------------+--------------+----------------+-------------------------------------------------------------------------------------------------+---------------+------------------+-----------------+-------------+--------------+----------+
|          Timestamp|Source IP Address|Destination IP Address|Source Port|Destination Port|Protocol|Packet Length|Packet Type|Traffic Type|                                                                                                                                          Payload Data|Malware Indicators|Anomaly Scores|Alerts/Warnings|Attack Type|Attack Signature|Action Taken|Severity Level|User Information|                                                                               Device Information|Network Segment| Geo-location Data|Proxy Information|Firewall Logs|IDS/IPS Alerts|Log Source|
+-------------------+-----------------+----------------------+-----------+----------------+--------+-------------+-----------+------------+------------------------------------------------------------------------------------------------------------------------------------------------------+------------------+--------------+---------------+-----------+----------------+------------+--------------+----------------+-------------------------------------------------------------------------------------------------+---------------+------------------+-----------------+-------------+--------------+----------+
|2023-05-30 08:33:58|    103.216.15.12|          84.9.164.252|      31225|           17616|    ICMP|          503|       Data|        HTTP|Qui natus odio asperiores nam. Optio nobis iusto accusamus ad perferendis esse at. Asperiores neque at ad.\nMaiores possimus ipsum saepe vitae. Ad ...|      IoC Detected|         28.67|           NULL|    Malware| Known Pattern B|      Logged|           Low|   Reyansh Dugal|                                  Mozilla/5.0 (compatible; MSIE 8.0; Windows NT 6.2; Trident/5.0)|      Segment A|Jamshedpur, Sikkim|     150.9.97.135|     Log Data|          NULL|    Server|
|2020-08-26 09:08:30|   78.199.217.198|        66.191.137.154|      17245|           48166|    ICMP|         1174|       Data|        HTTP|Aperiam quos modi officiis veritatis rem. Omnis nulla dolore perspiciatis.\nIllo animi mollitia vero voluptates error ad. Quidem maxime eaque optio...|      IoC Detected|          51.5|           NULL|    Malware| Known Pattern A|     Blocked|           Low|      Sumer Rana|                                  Mozilla/5.0 (compatible; MSIE 8.0; Windows NT 6.0; Trident/4.0)|      Segment B|Bilaspur, Nagaland|             NULL|     Log Data|          NULL|  Firewall|
|2022-11-13 09:23:25|     63.79.210.48|         198.219.82.17|      16811|           53600|     UDP|          306|    Control|        HTTP|                                                                          Perferendis sapiente vitae soluta. Hic delectus quae nemo ea esse est rerum.|      IoC Detected|         87.42|Alert Triggered|       DDoS| Known Pattern B|     Ignored|           Low|    Himmat Karpe|                                  Mozilla/5.0 (compatible; MSIE 9.0; Windows NT 6.2; Trident/5.0)|      Segment C| Bokaro, Rajasthan|   114.133.48.179|     Log Data|    Alert Data|  Firewall|
|2023-07-02 12:38:46|    163.42.196.10|       101.228.192.255|      20018|           32534|     UDP|          385|       Data|        HTTP|Totam maxime beatae expedita explicabo porro labore. Minima ab fugit officiis dicta perspiciatis pariatur. Facilis voluptates eligendi dolores even...|              NULL|         15.79|Alert Triggered|    Malware| Known Patte

Podemos contar el número de registros que tiene el dataset, y almacenarlo en una variable para su reutilización posterior

In [6]:
n_registros = df.count()
print(f"El dataset tiene {n_registros} registros")

El dataset tiene 40000 registros


# Descriptiva del dataset
Ahora invocaremos el método `summary` para obtener una descriptiva numérica de los campos que conforman nuestro dataset. Concretamente, se muestra la cuenta de valores no nulos, la media, desviación típica, mínimo, máximo y percentiles 25, 50 y 75.

In [7]:
df.summary()

+-------+-----------------+----------------------+------------------+-----------------+--------+-----------------+-----------+------------+------------------------------------------------------------------------------------------------------------------------------------------------------+------------------+------------------+---------------+-----------+----------------+------------+--------------+----------------+------------------------------------------------------------------+---------------+------------------------+-----------------+-------------+--------------+----------+
|summary|Source IP Address|Destination IP Address|       Source Port| Destination Port|Protocol|    Packet Length|Packet Type|Traffic Type|                                                                                                                                          Payload Data|Malware Indicators|    Anomaly Scores|Alerts/Warnings|Attack Type|Attack Signature|Action Taken|Severity Level|User Information|                                                Device Information|Network Segment|       Geo-location Data|Proxy Information|Firewall Logs|IDS/IPS Alerts|Log Source|
+-------+-----------------+----------------------+------------------+-----------------+--------+-----------------+-----------+------------+------------------------------------------------------------------------------------------------------------------------------------------------------+------------------+------------------+---------------+-----------+----------------+------------+--------------+----------------+------------------------------------------------------------------+---------------+------------------------+-----------------+-------------+--------------+----------+
|  count|            40000|                 40000|             40000|            40000|   40000|            40000|      40000|       40000|                                                                                                                                                 40000|             20000|             40000|          19933|      40000|           40000|       40000|         40000|           40000|                                                             40000|          40000|                   40000|            20149|        20039|         19950|     40000|
|   mean|             NULL|                  NULL|       32970.35645|      33150.86865|    NULL|       781.452725|       NULL|        NULL|                                                                                                                                                  NULL|              NULL|50.113473249999906|           NULL|       NULL|            NULL|        NULL|          NULL|            NULL|                                                              NULL|           NULL|                    NULL|             NULL|         NULL|          NULL|      NULL|
| stddev|             NULL|                  NULL|18560.425604487275|18574.66884156518|    NULL|416.0441918646553|       NULL|        NULL|                                                                                                                                                  NULL|              NULL|28.853598250518726|           NULL|       NULL|            NULL|        NULL|          NULL|            NULL|                                                              NULL|           NULL|                    NULL|             NULL|         NULL|          NULL|      NULL|
|    min|       1.1.45.194|           1.1.189.171|              1027|             1024|    ICMP|               64|    Control|         DNS|A ab tempora a. Culpa et fuga maxime. Quia ad blanditiis aliquam.\nFugit quia perferendis totam autem eum. Praesentium mollitia repellendus possimu...|      IoC Detected|               0.0|Alert Triggered|       DDoS| Known Pattern A|     Blocked|          High| Aaina Ahluwalia|Mozilla/5.0 (Android 1.0; Mobile; rv:14.0) Gecko/14.0 Firefox/14.0|     

No obstante, como puede apreciarse, esta descriptiva únicamente parece ser relevante para aquellas columnas que presentan valores numéricos (en este caso, únicamente `Source Port`, `Destination Port`, `Packet Length` y `Anomaly Scores`). Para el resto de campos nos interesa obtener otras descriptivas diferentes como por ejemplo la cantidad de valores únicos. Dicha funcionalidad no viene incorporada nativamente en PySpark, así que hay que calcularlo utilizando las funciones de SQL, que hemos importado en la variable `f`.

## Valores distintos

Nuestro objetivo, en resumen, es calcular el número de valores distintos que almacena cada una de las colúmnas de tipo string.

Para ello, en primer lugar vamos a mostrar cómo calcularíamos este número de valores distintos para una única columna, y posteriormente utilizaremos las herramientas que Python nos ofrece para generalizar a todas las columnas de tipo string.

Digamos que queremos hacer el cálculo para la columna `Severity Level`. Esto podemos hacerlo utilizando por ejemplo el método `select` del DataFrame, y con la función SQL `countDistinct`.

In [8]:
df.select(f.countDistinct("Severity Level").alias("Severity Level"))

+--------------+
|Severity Level|
+--------------+
|             3|
+--------------+

Observamos que dicha columna tiene tres valores distintos. Incluso podemos saber cuáles son mediante el método `distinct`.

In [9]:
df.select("Severity Level").distinct()

+--------------+
|Severity Level|
+--------------+
|          High|
|           Low|
|        Medium|
+--------------+

Veámos cuál es la estructura que subyace bajo este código. Claramente hay involucrados 3 métodos, que podemos enumerar según su orden de aparición:

1. `select`
2. `countDistinct`
3. `alias`

El método `select` acepta varios tipos de argumentos; entre ellos, se le puede pasar el resultado de una función de pyspark aplicado sobre una columna dada. Tal es nuestro caso, ya que le estamos pasando un único argumento, que es el siguiente:
```
f.countDistinct("Severity Level").alias("Severity Level")
```
Y este argumento consiste en una concatenación de dos métodos: uno llamado `countDistinct`, que es la función encargada de contar el número de valores distintos (aplicado en este caso a la columna `"Severity Level"`), y otro denominado `alias`, que como su nombre sugiere, renombra la columna resultante al nombre indicado (en este caso, el mismo nombre). Y es que si no incluyésemos este método `alias`, observemos qué pasaría:


In [10]:
df.select(f.countDistinct("Severity Level"))

+------------------------------+
|count(DISTINCT Severity Level)|
+------------------------------+
|                             3|
+------------------------------+

Fijémonos en el nombre de la columna que se pone por defecto: `count(DISTINCT Severity Level)`. No es un nombre muy user-friendly para luego utilizarlo en posibles transformaciones posteriores. Es por ello lo de usar el método `alias` para devolver el nombre de la columna del resultado de la operación a su valor original.

Bien, hemos calculado el número de valores distintos para una única columna de tipo texto. Ahora vamos un pequeño paso más allá, y hagamos lo mismo pero para dos columnas, por ejemplo `Security Level` y `Traffic Type`. La generalización es muy sencilla:

In [11]:
df.select(
    [
        f.countDistinct("Severity Level").alias("Security Level"),
        f.countDistinct("Traffic Type").alias("Traffic Type"),
    ]
)

+--------------+------------+
|Security Level|Traffic Type|
+--------------+------------+
|             3|           3|
+--------------+------------+

Como es puede comprobar, lo único que hemos hecho es pasarle ahora como argumento al método `select` una lista, y cada uno de los elementos de esta lista ejecuta la misma operación que hemos visto en el caso del cálculo para una única columna: aplica la función de pyspark `countDistinct` a la columna correspondiente y después le asigna un alias para renombrarlo de su manera original.

Ahora bien, para estos casos en los que estamos ejerciendo el cálculo sobre unas pocas columnas, todavía es viable escribir cada una de las expresiones a mano como hemos hecho, sin embargo, ¿qué ocurrirá cuando tengamos, digamos 100 o más columnas? ¿escribiríamos un código monstruoso de la siguiente manera?
```python
df.select(
    [
        f.countDistinct("col 1").alias("col 1"),
        f.countDistinct("col 2").alias("col 2"),
        f.countDistinct("col 3").alias("col 3"),
        ...
        f.countDistinct("col 100").alias("col 100"),
    ]
)
```
Naturalmente esto resulta inviable, y lo que tiene sentido en este caso es aprovechar la automatización que nos ofrece Python. Este es un caso en el que el concepto de `list comprehension` nos ayudaría. Con esta herramienta, podemos crear, utilizando una sola línea de código, listas de elementos a partir de otros iterables, e incluso filtrar según condicionales.

Por ejemplo, supongamos que tenemos una lista de frutas:

In [12]:
fruits = ["apple", "banana", "cherry", "kiwi", "mango"]

y ahora queremos obtener otra lista de frutas a partir de esta, pero filtrando únicamente aquellos elementos que contengan la letra `"a"`. Utilizando list comprehension, podemos incorporar el bucle dentro de la propia lista, y en una única línea de código lo tenemos:

In [13]:
[fruit for fruit in fruits if "a" in fruit]

['apple', 'banana', 'mango']

Bien, pues utilizando este concepto, aplicado a nuestro caso, lo que haremos será iterar por el esquema de nuestro dataset, de manera que los elementos de la lista serán el resultado de los cálculos, y filtraremos únicamente aquellos campos que son de tipo texto. Esto, traducido a código, sería:
<a id="valores-distintos"></a>

In [14]:
df.select(
    [
        f.countDistinct(c.name).alias(c.name)
        for c in df.schema.fields
        if isinstance(c.dataType, t.StringType)
    ]
)

+-----------------+----------------------+--------+-----------+------------+------------+------------------+---------------+-----------+----------------+------------+--------------+----------------+------------------+---------------+-----------------+-----------------+-------------+--------------+----------+
|Source IP Address|Destination IP Address|Protocol|Packet Type|Traffic Type|Payload Data|Malware Indicators|Alerts/Warnings|Attack Type|Attack Signature|Action Taken|Severity Level|User Information|Device Information|Network Segment|Geo-location Data|Proxy Information|Firewall Logs|IDS/IPS Alerts|Log Source|
+-----------------+----------------------+--------+-----------+------------+------------+------------------+---------------+-----------+----------------+------------+--------------+----------------+------------------+---------------+-----------------+-----------------+-------------+--------------+----------+
|            40000|                 40000|       3|          2|           3|       40000|                 1|              1|          3|               2|           3|             3|           32389|             32104|              3|             8723|            20148|            1|             1|         2|
+-----------------+----------------------+--------+-----------+------------+------------+------------------+---------------+-----------+----------------+------------+--------------+----------------+------------------+---------------+-----------------+-----------------+-------------+--------------+----------+

Esta es la tabla con el número de valores únicos por cada una de las columnas de tipo texto.

**Resúmen de la list comprehension**
- **Iterable original** (el equivalente a la lista de frutas que hemos visto en el ejemplo anterior): `df.schema.fields`. Se trata de una lista de elementos igual (las columnas/tipos del dataframe), pero estos elementos son más complejos que simples cadenas de texto como en el caso de las frutas. Son otros objetos, que entre otros atributos tienen un nombre (`name`) que es el nombre de cada columna, y un tipo (`dataType`) que es el tipo asociado a dicha columna.
- **Elementos**: en este caso, en lugar de mostrar los elementos originales de la lista de partida, como en el caso de ejemplo de las frutas, lo que mostramos es el resultado de la función `countDistinct` aplicado a cada columna, seguido por el renombrado con `alias` correspondiente.
- **Filtro**: en este caso el filtro es la condición `isinstance(c.dataType, t.StringType)`, que viene a decirnos que nos quedemos únicamente con los elementos cuyo tipo (el atributo `dataType`) sea de tipo string (`t.StringType`)


## Gráficas univariadas
Continuando con nuestro análisis, y teniendo en cuenta estos resultados de los valores únicos por cada columna de tipo texto, observamos que no todas las columnas textuales presentan la misma cardinalidad. Por ejemplo, las columnas `"Source IP Address"` y `"Destination IP Address"` contienen tantos valores únicos como registros tiene el propio dataset, es decir, no pueden aportar ningún tipo de información agregada. La entropía de estas columnas es 0.

*Nota*: que una columna contenga una cardinalidad muy elevada (y por tanto, muy baja entropía, y poca información), no implica que a partir de la misma no puedan extraerse otros campos derivados que sí contengan una cardinalidad menor. Por ejemplo, veamos cómo la cardinalidad de la columna `Timestamp` es muy elevada:

In [15]:
df.select(
    (f.countDistinct("Timestamp") / f.count("*")).alias("ratio_timestamp_distintos")
)

+-------------------------+
|ratio_timestamp_distintos|
+-------------------------+
|                 0.999925|
+-------------------------+

Sin embargo, a partir de esta columna, podríamos construir un campo derivado, llamado `Year`, que presenta una cardinalidad muchisimo menor:

In [16]:
df.select(f.countDistinct(f.year("Timestamp")).alias("anyos_distintos"))

+---------------+
|anyos_distintos|
+---------------+
|              4|
+---------------+

Ya que nuestro dataset, aunque abarca un enorme rango de fechas a nivel de granularidad de hora, cuando disminuimos la granularidad a nivel de año, únicamente abarca 4 años distintos.

Para el resto de variables que sí parece que representan categorías (con una cardinalidad pequeña), podemos estudiar su distribución mediante un diagrama de barras. Pero para ello, en primer lugar necesitamos realizar una agrupación de sus valores, seguido de un conteo de cada uno de los grupos. Para ello, haremos uso del método `groupBy`, seguido de una operación de agregación, que consiste en calcular la frecuencia de aparición de cada uno de esos grupos (con respecto al total de registros).

Finalmente, convertimos el DataFrame resultante a un DataFrame de pandas, ya que las librerías gráficas habitualmente solo trabajan con DataFrames de pandas, no de PySpark. Para ello, llamamos al método `toPandas`:

In [17]:
protocolos_hist = (
    df.groupBy("Protocol").agg((f.count("*") / n_registros).alias("freq")).toPandas()
)
# Ahora la variable `protocolos_hist` es un dataframe de pandas, no de spark
display(protocolos_hist)

Protocol      freq
0     ICMP  0.335725
1      UDP  0.332475
2      TCP  0.331800

Una vez completada la conversión a pandas mediante el método `toPandas`, podemos utilizar la librería de `plotly` para visualizar gráficos interactivos.

Por ejemplo, para variables categóricas, como la que acabamos de ver (`Protocol`), podemos utilizar la función `bar` del módulo `plotly.express`, que hemos importado y asignado al alias `px`. A esta función, le pasaremos dos argumentos base:
- `x`: los valores que presenta la columna categórica. En este caso, le pasamos toda la serie de valores `protocolos_hist.Protocol`.
- `y`: los valores de las frecuencias asociadas a cada valor de la columna categórica. En este caso, se corresponde con los valores del campo `protocolos_hist.freq`.

El resto de argumentos simplemente responden al diseño del gráfico, como el ajuste del ancho (`width`), el título (`title`) o las etiquetas que se añadirán a los ejes horizontal y vertical (`labels`)

In [18]:
fig = px.bar(
    x=protocolos_hist.Protocol,
    y=protocolos_hist.freq,
    width=500,
    title="Distribución del protocolo",
    labels=dict(x="Protocolo", y="frecuencia"),
)
fig.update_layout(title_x=0.5)

Podemos hacer lo mismo para otras variables categóricas como la del tipo de ataque (`Attack Type`)

In [19]:
attacks_hist = (
    df.groupBy("Attack Type").agg((f.count("*") / n_registros).alias("freq")).toPandas()
)
display(attacks_hist)

Attack Type      freq
0   Intrusion  0.331625
1        DDoS  0.335700
2     Malware  0.332675

In [20]:
fig = px.bar(
    x=attacks_hist["Attack Type"],
    y=attacks_hist.freq,
    width=500,
    title="Distribución del tipo de ataque",
    labels=dict(x="Tipo de Ataque", y="frecuencia"),
)
fig.update_layout(title_x=0.5)

Para variables de tipo numérico, como la longitud del paquete (`Packet Length`), podemos hacer uso de la función `histogram` del paquete de visualización de `plotly`. A dicha función le pasaremos un array o lista unidimensional con los valores de la variable de estudio, y ella se encargará de categorizar los datos mediante diferentes rangos de valores o binnings.

In [21]:
fig = px.histogram(
    x=[i[0] for i in df.select("Packet Length").collect()],
    nbins=1000,
    title="Distribución de la longitud del paquete",
    histnorm="probability density",
    labels=dict(x="Longitud de paquete"),
    width=1000,
)
fig.update_layout(title_x=0.5)

In [22]:
fig = px.histogram(
    x=[i[0] for i in df.select("Anomaly Scores").collect()],
    nbins=1000,
    title="Distribución de los scoring de anomalías",
    histnorm="probability density",
    labels=dict(x="Scoring anomalía"),
    width=1000,
)
fig.update_layout(title_x=0.5)

Notar que hemos hecho uso del método `collect`, que coleccionará todos los datos del DataFrame resultante al driver. Hay que tener cuidado al utilizar esta función, y asegurarse que el volúmen de datos que va a coleccionarse es relativamente pequeño.

Ahora probemos con un cálculo más avanzado. Podemos establecer nuestro propio rango de binnings para variables numéricas, como por ejemplo el puerto de destino (`Destination Port`). Para ello dividiremos todo el rango de valores de dicha variable en el número de binnings que deseemos (por ejemplo, 5), y haciendo uso de los métodos `groupBy` y `when`, agruparemos según el binning en el que caiga cada registro. Finalmente, pivotamos los valores de la columna `Attack Type` hacia diferentes columnas y contamos la frecuencia de cada grupo.

In [23]:
min_port, max_port = df.select(
    f.min("Destination Port"), f.max("Destination Port")
).collect()[0]
print(min_port, max_port)

1024 65535


Dividimos el rango de los puertos de destino en 5 binnings, y para ello hacemos uso de la división entera de Python (`//`)

In [24]:
port_diff = (max_port - min_port) // 5
print(port_diff)

12902


In [25]:
rangos_puertos = (
    df.groupBy(
        f.when(
            f.col("Destination Port").between(min_port, min_port + port_diff),
            f.lit(f"[{min_port}, {min_port + port_diff}]"),
        )
        .when(
            f.col("Destination Port").between(
                min_port + port_diff + 1, min_port + 2 * port_diff
            ),
            f.lit(f"[{min_port + port_diff + 1}, {min_port + 2*port_diff}]"),
        )
        .when(
            f.col("Destination Port").between(
                min_port + 2 * port_diff + 1, min_port + 3 * port_diff
            ),
            f.lit(f"[{min_port + 2*port_diff + 1}, {min_port + 3*port_diff}]"),
        )
        .when(
            f.col("Destination Port").between(
                min_port + 3 * port_diff + 1, min_port + 4 * port_diff
            ),
            f.lit(f"[{min_port + 3*port_diff + 1}, {min_port + 4*port_diff}]"),
        )
        .when(
            f.col("Destination Port").between(
                min_port + 4 * port_diff + 1, min_port + 5 * port_diff + 1
            ),
            f.lit(f"[{min_port + 4*port_diff + 1}, {min_port + 5*port_diff+1}]"),
        )
        .alias("port_range")
    )
    .pivot("Attack Type")
    .agg(f.count("*") / n_registros)
)

display(rangos_puertos)

+--------------+--------+---------+--------+
|    port_range|    DDoS|Intrusion| Malware|
+--------------+--------+---------+--------+
|[13927, 26828]|  0.0677| 0.068575|0.067025|
|[52633, 65535]|0.066875| 0.065975|  0.0642|
| [1024, 13926]| 0.06705| 0.065325|0.067575|
|[39731, 52632]|0.067825| 0.066175|  0.0676|
|[26829, 39730]| 0.06625| 0.065575|0.066275|
+--------------+--------+---------+--------+

Podemos visualizar esta tabla en un gráfico de barras

In [26]:
fig = rangos_puertos.pandas_api("port_range").plot.bar(
    title="Distribución del tipo de ataque según rangos de puertos",
    labels="df",
    width=1000,
)
fig.update_layout(title_x=0.5)

/home/dadiego/projects/ESIC/esic-bigdata-iv-blackops/.venv/lib/python3.10/site-packages/pyspark/pandas/__init__.py:50: UserWarning:

'PYARROW_IGNORE_TIMEZONE' environment variable was not set. It is required to set this environment variable to '1' in both driver and executor sides if you use pyarrow>=2.0.0. pandas-on-Spark will set it for you but it does not work if there is a Spark context already launched.



Como se aprecia, parecemos estar ante un dataset muy preparado, puesto que la distribución de todas las variables tanto numéricas como categóricas que hemos analizado es muy uniforme

# Extracción de nuevos campos
En numerosas ocasiones nos resultará de utilidad añadir algunos campos derivados a partir del contenido de otros existentes, ya que la información puede sernos de gran interés. Por ejemplo, la columna `Device Information` parece que contiene texto en el cual se indica, entre otras cosas, el navegador, y el tipo de dispositivo que origina la conexión. Entonces vamos a tratar de extraer esta información en un nuevo campo que será categórico.

Veamos que pinta tiene esta columna original, y para ello sampleamos aleatoriamente 5 registros:
<a id="device-info"></a>

In [27]:
df.select("Device Information").sample(0.1, seed=25).limit(5)

+---------------------------------------------------------------------------------------------------------------+
|                                                                                             Device Information|
+---------------------------------------------------------------------------------------------------------------+
|                                                Mozilla/5.0 (compatible; MSIE 9.0; Windows NT 5.0; Trident/5.1)|
|Mozilla/5.0 (Windows; U; Windows NT 5.0) AppleWebKit/531.24.5 (KHTML, like Gecko) Version/5.0.4 Safari/531.24.5|
|                                              Opera/9.51.(X11; Linux i686; byn-ER) Presto/2.9.185 Version/12.00|
|                                                    Opera/8.73.(Windows CE; as-IN) Presto/2.9.164 Version/12.00|
|           Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/533.0 (KHTML, like Gecko) Chrome/39.0.895.0 Safari/533.0|
+---------------------------------------------------------------------------------------------------------------+

Parece ser que el texto presente antes de la barra `/` se corresponde con el navegador (ej: Mozilla, Opera). Vale, pues entonces podemos crear una nueva columna, a la que llamaremos `Browser`, que almacene esta información. Para ello, lo que tendremos que hacer es utilizar la función `split` de PySpark, para dividir el texto en diferentes partes de acuerdo al símbolo `/`. El resultado de esta operación es un array (lista), en la que el primer elemento del array (`[0]`) contendrá la información del navegador, porque es lo que queda a la izquierda del símbolo `/`. Veámoslo

In [28]:
df = df.withColumn("Browser", f.split("Device Information", "/")[0])

# Mostramos 3 registros aleatorios de la nueva columna Browser, para ver el resultado de esta operación
display(df.select("Browser").sample(0.1, seed=25).limit(3))

+-------+
|Browser|
+-------+
|Mozilla|
|Mozilla|
|  Opera|
+-------+

Fenomenal, pero no solo podemos extraer la información del navegador de origen, también vemos en la [celda 27](#device-info) que se muestra otra información como el sistema operativo o dispositivo utilizado (Linux, Windows, Android, Ipad, Ipod, Iphone, Macintosh).

Vamos entonces a añadir otro campo para almacenar estas categorías. Para ello, usamos en este caso la función `regexp_extract`, que nos permite extraer un patrón de texto dentro de una cadena de texto más grande. Nuestro patrón vendrá definido por los diferentes SOs que hemos observado que aparecen en la columna original: `"(windows|linux|android|ipad|ipod|iphone|macintosh)"`. El argumen to `idx=0` nos indica que nos quedemos con el primer elemento que aparezca, y la función `lower` la utilizamos para que la búsqueda sea case-insensitive (que no dependa de mayúsculas o minúsculas).

In [29]:
df = df.withColumn(
    "Operating System",
    f.regexp_extract(
        f.lower("Device Information"),
        pattern=r"(windows|linux|android|ipad|ipod|iphone|macintosh)",
        idx=0,
    ),
).drop("Device Information")

Observemos que al final de la operación hemos encadenado el método `.drop("Device Information")`, para eliminar la columna original `Device Information`, que ya no nos es necesaria, puesto que ya hemos extraído la información que necesitábamos de la misma.

También podemos extraer algunos campos derivados del campo de fecha (`Timestamp`), como pueden ser el año, mes, día y hora. Así podremos realizar algún análisis de periodicidad, para ver cómo evolucionan los ataques según la época del año.

In [30]:
df = df.withColumns(
    {
        "Year": f.year("Timestamp"),
        "Month": f.month("Timestamp"),
        "Day": f.day("Timestamp"),
        "Hour": f.hour("Timestamp"),
    }
).drop("Timestamp")

Por último, recordemos que cuando calculamos los [valores distintos](#valores-distintos) de los campos de texto, vimos que había algunos, como `Malware Indicators`, `Alerts/Warnings`, `Firewall Logs`, `IDS/IPS Alerts` que únicamente presentaban un valor. Es decir, o bien tienen una categoría, o bien vienen en nulo. Por tanto realmente se trata de variables binarias, que podemos codificar como 1 (que contengan un valor) o 0 (que no contengan valor). Vamos a transformarlas a este tipo, ya que facilita los análisis posteriores y los eventuales modelos predictivos que pudieran hacerse.

In [31]:
df = df.withColumns(
    {
        "Malware Indicators": f.when(
            f.col("Malware Indicators").isNotNull(), 1
        ).otherwise(0),
        "Alerts/Warnings": f.when(f.col("Alerts/Warnings").isNotNull(), 1).otherwise(0),
        "Firewall Logs": f.when(f.col("Firewall Logs").isNotNull(), 1).otherwise(0),
        "IDS/IPS Alerts": f.when(f.col("IDS/IPS Alerts").isNotNull(), 1).otherwise(0),
    }
)

Veamos cómo ha quedado nuestro dataframe final, después de todas estas transformaciones y creación de nuevos campos

In [32]:
df.sample(0.1, seed=42).limit(5)

+-----------------+----------------------+-----------+----------------+--------+-------------+-----------+------------+------------------------------------------------------------------------------------------------------------------------------------------------------+------------------+--------------+---------------+-----------+----------------+------------+--------------+----------------+---------------+-----------------------------+-----------------+-------------+--------------+----------+-------+----------------+----+-----+---+----+
|Source IP Address|Destination IP Address|Source Port|Destination Port|Protocol|Packet Length|Packet Type|Traffic Type|                                                                                                                                          Payload Data|Malware Indicators|Anomaly Scores|Alerts/Warnings|Attack Type|Attack Signature|Action Taken|Severity Level|User Information|Network Segment|            Geo-location Data|Proxy Information|Firewall Logs|IDS/IPS Alerts|Log Source|Browser|Operating System|Year|Month|Day|Hour|
+-----------------+----------------------+-----------+----------------+--------+-------------+-----------+------------+------------------------------------------------------------------------------------------------------------------------------------------------------+------------------+--------------+---------------+-----------+----------------+------------+--------------+----------------+---------------+-----------------------------+-----------------+-------------+--------------+----------+-------+----------------+----+-----+---+----+
|     11.48.99.245|        178.157.14.116|      34489|           20396|    ICMP|         1022|       Data|         DNS|Amet libero optio quidem praesentium libero. Ea magnam atque corporis ipsum iure iusto.\nEveniet dolor odio libero. Minus iste fugit asperiores min...|                 1|         54.05|              1|  Intrusion| Known Pattern A|      Logged|          High|    Yuvaan Dubey|      Segment A|     Phagwara, Andhra Pradesh|     192.31.159.5|            1|             1|  Firewall|Mozilla|       macintosh|2023|    2| 12|   8|
|    4.255.187.165|       136.159.186.239|      39934|            5259|     TCP|          838|    Control|        HTTP|Sed facere culpa aliquam. Adipisci error quisquam reprehenderit itaque fugit illum. Minima exercitationem occaecati nemo repudiandae officia quasi....|                 0|         43.83|              1|       DDoS| Known Pattern B|     Ignored|          High|   Samarth Ratti|      Segment B|           Solapur, Telangana|             NULL|            1|             0|    Server|  Opera|         windows|2023|    4| 18|  18|
|  119.101.120.119|          47.125.34.52|       4510|           26783|     TCP|          124|    Control|         DNS|Qui sapiente laboriosam minima veritatis impedit vel. Placeat itaque incidunt non. Consequuntur quo quod.\nRecusandae similique explicabo error lab...|                 0|         44.75|              1|       DDoS| Known Pattern B|     Ignored|          High|    Faiyaz Sathe|      Segment C|            Rampur, Rajasthan|             NULL|            0|             0|  Firewall|Mozilla|         windows|2020|   12| 29|   3|
|    122.130.86.58|         110.54.165.63|      49005|           19289|    ICMP|          317|       Data|        HTTP|                                                        Officia tenetur aliquam facere quasi numquam. Assumenda similique quisquam facilis porro nisi.|                 1|         56.92|              0|       DDoS| Known Pattern A|     Ignored|           Low| Mohanlal Talwar|      Segment A|Medininagar, Himachal Pradesh|    79.251.62.155|            1|             1|    Server|Mozilla|         windows|2023|    1| 18|   2|
|   123.233.44.106|        154.223.194.82|      38169|            9878|     TCP|         1497|    Control|        HTTP|                                                                         

# Visualizaciones de datos

In [33]:
fig = (
    df.groupBy("Day")
    .pivot("Malware Indicators")
    .agg(f.count("*"))
    .pandas_api("Day")
    .plot.bar(title="<b>Distribución de indicadores de Malware por día</b>", width=1000)
)
fig.update_layout(title_x=0.5, legend_title_text="Malware Indicator")
fig.update_traces(hovertemplate="<b>Day: %{x}</b><br>Cantidad de registros: %{y}")

In [34]:
fig = (
    df.groupBy("Month")
    .pivot("Malware Indicators")
    .agg(f.count("*"))
    .pandas_api("Month")
    .plot.bar(title="<b>Distribución de indicadores de Malware por mes</b>", width=1000)
)
fig.update_layout(title_x=0.5, legend_title_text="Malware Indicator")
fig.update_traces(hovertemplate="<b>Month: %{x}</b><br>Cantidad de registros: %{y}")

In [35]:
fig = (
    df.groupBy("Year")
    .pivot("Malware Indicators")
    .agg(f.count("*"))
    .pandas_api("Year")
    .plot.bar(title="<b>Distribución de indicadores de Malware por año</b>", width=1000)
)
fig.update_layout(title_x=0.5, legend_title_text="Malware Indicator")
fig.update_traces(hovertemplate="<b>Year: %{x}</b><br>Cantidad de registros: %{y}")

In [36]:
df.groupBy("Traffic Type").count().pandas_api("Traffic Type").plot.pie(
    y="count", width=1000, title="Traffic Type Distribution"
)

In [37]:
df.groupBy("Browser").count().pandas_api("Browser").plot.pie(
    y="count", width=1000, title="Browser Distribution"
)

In [38]:
df.groupBy("Operating System").count().pandas_api("Operating System").plot.pie(
    y="count", width=1000, title="Operating System Distribution"
)